# Import Packages

In [72]:
import pandas as pd
import numpy as np
import time
import random
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from json import loads, dumps

# Create Interceptor

In [16]:
USER_AGENT = '"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36"'
SEC_CH_UA = '\"Google Chrome\";v=\"123\", \"Not:A-Brand\";v=\"8\", \"Chromium\";v=\"123\"'
REFERER = "https://www.google.com"

def interceptor(request):
    del request.header["user-agent"]
    request.header["user-agent"] = USER_AGENT
    request.header["sec-ch-ua"] = SEC_CH_UA
    request.header["referer"] = REFERER

# Initialise Web Driver and Scrape

In [77]:
# Creating the webdriver
driver = webdriver.Chrome()
driver.request_interceptor = interceptor
driver.maximize_window()

base_url = "https://www.elitigation.sg/gdviewer/s/{year}_{court}_{case_id}"

years = range(2000, 2024)
courts = ['SGHC', 'SGCA']
case_ids = range(1, 430)

def clean(text):
    print(text)
    lookup = {}
    current_key = None
    for element in text:
        if element[0] == "Header: ":
            current_key = element[1]
            lookup[current_key] = []
        else:
            if current_key is None:
                continue
            lookup[current_key] += element
    return lookup

def get(collection, key="fact"):
    if key == "fact":
        get_fact(collection)
    elif key == "issue":
        get_issue(collection)
    else:
        print("No such key.")

def get_fact(collection):
    keywords = ["Background", "background", "Fact", "fact", "Facts", "facts"]
    for key in collection.keys():
        for keyword in keywords:
            if keyword in key:
                return collection[key]

def get_issue(collection):
    pass

temp_df = pd.DataFrame(columns=["filename", "fact"])
temp_df_1 = pd.read_json(r"rawish_data\facts.json", lines=True)

lookup = {}

for year in years:
    for court in courts:
        for case_id in case_ids:
            case_url = base_url.format(year=year, court=court, case_id=case_id)
            driver.get(case_url)
            containers = driver.find_elements(By.XPATH, '//*[contains(@class, "Judg-Heading-1 text-left  font-weight-bold") or contains(@class, "Judg-1 mb-3 text-justify") or contains(@class, "Judg-2 mb-3 text-justify")]')
            if not containers:
                continue
            x = []  
            x.extend(list(map(lambda x: ["Header: "] + x.text.split("\n") if "Judg-Heading-1 text-left  font-weight-bold" in x.get_attribute("class") else x.text.split("\n"), containers)))
            sec = random.randint(1, 10)
            time.sleep(sec)
            cleaned_text = clean([y for y in x])
            lookup[f"{year}_{court}_{case_id}"] = cleaned_text
            temp_df.loc[len(temp_df.index)] = [f"{year}_{court}_{case_id}", get_fact(cleaned_text)]
            temp_df

            # Cross check with PyPDF extracted facts
            temp_df_1_2023 = temp_df_1[temp_df_1["casename"].str.contains(f"{year}_{court}")]
            temp_df_1_2023["casename"] = temp_df_1_2023["casename"].apply(lambda x: x[:-4])
            temp_df_1_2023.reset_index(inplace=True)
            temp_df_1_2023

            # Clean the extracted data from scraping
            temp_df["fact"] = temp_df["fact"].apply(lambda x: "" if x is None else x)

            temp_df["fact"] = temp_df["fact"].astype("string")

            temp_df["fact"] = temp_df["fact"].apply(lambda x: x[1:-1] if x != "" else x)
            temp_df

            # Merge the 2 dataframes (web scraped and PyPDF)
            merged_df = pd.merge(temp_df_1_2023, temp_df, left_on="casename", right_on="filename", how="left")
            merged_df

            # Merge all the facts extracted by both web scrapper and PyPDF
            merged_df_copy = merged_df.copy(deep=True)
            merged_df_copy["fact"] = merged_df_copy.apply(lambda x: x["facts"] if (x["fact"] == "" or x["fact"] is np.NaN) else x["fact"], axis=1) 
            merged_df_copy.drop(columns=["index", "facts", "filename"], inplace=True)
            merged_df_copy

            # Save to json
            file = f"{year}_{court}_facts.json"
            merged_df_copy.to_json(file, orient="records", lines=True)

            

driver.quit()

[['Header: ', 'Introduction'], ['1\u2003Counterfeit goods are the bane and blight of trade mark proprietors. In asserting and enforcing their rights, it is usual for trade mark proprietors to target the manufacturers or wholesalers of such goods as they are the most culpable and probably profit the most from their illegal activities.'], ['2\u2003However, in the present case, two trade mark proprietors commenced an infringement of trade marks action against a freight forwarder in Singapore for importing counterfeit goods by sea. On the available evidence before the court, the freight forwarder’s involvement in the transaction was only to receive the cargo from one country (China) and to forward it to another country (Indonesia). The goods were in sealed containers and were never placed on or intended for the Singapore market and were not seen by any consumers in Singapore. It is not disputed that the freight forwarder did not see or handle the goods physically while they were in transit